In [1]:
import os
import sys

import IPython.display as IPDisplay

class TOC:
    __titleTemplate = "{titlePref} {title}"
    __tocTemplate = "{title}\n---\n{entries}"
    __entryTemplate = "{tabPref}{id}. {title}\n"
    
    def __init__(self, title, toc=[], tocLevel=2):
        self._toc = toc
        self._title = title
        self._level = tocLevel
    
    def title(self, *ids):
        prefix = "#"*min(self._level, (1+len(ids)))
        if len(ids) == 0:
            title = self._title
        else:
            entry = (None, self._toc)
            for i in ids:
                entry = entry[1][i]
            title = f"{'.'.join(str(1+i) for i in ids)}. {entry[0]}"
        return TOC.__titleTemplate.format(titlePref=prefix, title=title)
    
    def entries(self, toc, ids, depth=0):
        entries = ""
        tabPref = "\t"*depth
        for i, (title, subToc) in enumerate(toc):
            subEntries = ""
            if ids:
                if ids[0] == i:
                    title = f"__{title}__"
                    subEntries = self.entries(subToc, ids[1:], depth+1)
                elif ids[0] < 0:
                    subEntries = self.entries(subToc, ids[1:], depth+1)
            entry = TOC.__entryTemplate.format(tabPref=tabPref, id=i+1, title=title)
            entries = f"{entries}{entry}{subEntries}"
        return entries
    
    def display(self, *ids):
        title = self.title(*ids)
        if len(ids) == 0: ids = (-1,)*(self._level - 1)
        return TOC.__tocTemplate.format(title=title, entries=self.entries(self._toc, ids))

In [2]:
import pathlib

pathlib.Path("kernProfOut/").mkdir(exist_ok=True)

In [3]:
__toc = TOC(
    "How to write parallel python code", [(
    "Toy problem", [
        ("Matrix multiplication", []),
        ("Code example", []),
    ]), (
    "Profiling", [
        ("Test data (benchmark)", []),
        ("Driver program", []),
    ]), (
    "Vectorisation", [
        ("Array programming", [
            ("Indexing", []),
            ("Broadcasting", []),
        ]),
        ("SIMD", [
            ("Data type", []),
            ("Memory layout", []),
        ]),
    ]), (
    "Parallel execution", [
        ("Multi-threading/processing", [
            ("Concepts", []),
            ("The python situation", []),
        ]),
        ("Data & Memory", [
            ("Shared memory Vs messages", []),
            ("Concurrent access", []),
        ]),
    ]), (
    "Wrapping up", [
    ]),
], tocLevel=1)

In [4]:
IPDisplay.Markdown(__toc.display())

# How to write parallel python code
---
1. Toy problem
2. Profiling
3. Vectorisation
4. Parallel execution
5. Wrapping up


In [5]:
IPDisplay.Markdown(__toc.display(0))

# 1. Toy problem
---
1. __Toy problem__
	1. Matrix multiplication
	2. Code example
2. Profiling
3. Vectorisation
4. Parallel execution
5. Wrapping up


In [6]:
matTxt = r"""$C_{(m\times n)} = \begin{bmatrix}
    c_{00} & \dots & c_{0j} & \dots & c_{0n}\\
    \vdots & \ddots & \vdots & & \vdots\\
    c_{i0} & \dots & c_{ij} & \dots & c_{in}\\
    \vdots & & \vdots & \ddots & \vdots\\
    c_{m0} & \dots & c_{mj} & \dots & c_{mn}
\end{bmatrix}$"""

matMulShapes = r"""$A_{(m\times l)} \cdot B_{(l\times n)} = C_{(m\times n)}$"""
matMulEq = r"""$c_{ij} = \Sigma_{k}^{l}(a_{ik} \cdot b_{kj})$"""

IPDisplay.Markdown(f"""
{__toc.title(0, 0)}
---
For three matrices $A$, $B$ and $C$ such that {matMulShapes}

The elements of matrix $C$ noted as {matTxt}

Are computed as follows: {matMulEq}
""")


# 1.1. Matrix multiplication
---
For three matrices $A$, $B$ and $C$ such that $A_{(m\times l)} \cdot B_{(l\times n)} = C_{(m\times n)}$

The elements of matrix $C$ noted as $C_{(m\times n)} = \begin{bmatrix}
    c_{00} & \dots & c_{0j} & \dots & c_{0n}\\
    \vdots & \ddots & \vdots & & \vdots\\
    c_{i0} & \dots & c_{ij} & \dots & c_{in}\\
    \vdots & & \vdots & \ddots & \vdots\\
    c_{m0} & \dots & c_{mj} & \dots & c_{mn}
\end{bmatrix}$

Are computed as follows: $c_{ij} = \Sigma_{k}^{l}(a_{ik} \cdot b_{kj})$


In [7]:
IPDisplay.Markdown(f"""
{__toc.title(0, 0)}
---
{matMulEq}
""")


# 1.1. Matrix multiplication
---
$c_{ij} = \Sigma_{k}^{l}(a_{ik} \cdot b_{kj})$


<div class="full-width">
  <div class="column" style="float: left; width: 25%; height: auto">
    <!-- img src="assets/MatrixMultiplication.gif" alt="MatrixMultiplication"/-->
    <img src="https://miro.medium.com/v2/resize:fit:872/1*oy1_SOkKGIhP0PAoWolNTw.gif" alt="MatrixMultiplication"/>
  </div>
  <div class="column" style="float: right; width: 75%">
    <h4>For each element $c_{ij}$ of $C$</h4>
    <ol>
        <li><u>Select</u>:
            <ul>
                <li>The $i^{th}$ <b>row</b> of $A$</li>
                <li>The $j^{th}$ <b>column</b> of $B$</li>
            </ul>
        </li>
        <li><u>Multiply</u> $a_{i\cdot}$ and $b_{\cdot j}$ <b>element-wise</b></li>
        <li><u><b>Reduce</b></u> the result with a sum operation</li>
    </ol>
  </div>
</div>

In [8]:
IPDisplay.Markdown(__toc.display(0, 1))

# 1.2. Code example
---
1. __Toy problem__
	1. Matrix multiplication
	2. __Code example__
2. Profiling
3. Vectorisation
4. Parallel execution
5. Wrapping up


In [9]:
IPDisplay.Markdown(f"""
{__toc.title(0, 1)}
---
""")


# 1.2. Code example
---


In [10]:
import numpy as np

def matMulElem(aRow, bCol, l):
    cij = 0
    for k in range(l):
        ab = aRow[k] * bCol[k]  # multiply element-wise
        cij += ab  # reduce with a sum
    return cij

def matMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    C = np.empty((m, n), dtype=A.dtype)
    for i in range(m):
        for j in range(n):
            C[i, j] = matMulElem(A[i, :], B[:, j], l)
    return C

In [11]:
IPDisplay.Markdown(__toc.display(1))

# 2. Profiling
---
1. Toy problem
2. __Profiling__
	1. Test data (benchmark)
	2. Driver program
3. Vectorisation
4. Parallel execution
5. Wrapping up


In [12]:
IPDisplay.Markdown(f"""
{__toc.title(1, 0)}
---
""")


# 2.1. Test data (benchmark)
---


In [13]:
def produceMatrices(m, n, l):
    A = np.random.rand(m, l).astype(np.float64)
    B = np.random.rand(l, n).astype(np.float64)
    return A, B, A@B

matricesLowL = [  # !! Use the same data across different runs
    produceMatrices(200, 400, 10)
    for _ in range(10)  # !! Have several (different) samples
]

matricesHighL = [  # !! Use the same data across different runs
    produceMatrices(20, 40, 10000)
    for _ in range(10)  # !! Have several (different) samples
]

In [14]:
IPDisplay.Markdown(f"""
{__toc.title(1, 1)}
---
""")


# 2.2. Driver program
---


In [15]:
nRuns = 10

def runMainLowL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesLowL:
            C = matMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def runMainHighL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesHighL:
            C = matMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def main():
    runMainLowL()
    runMainHighL()

In [16]:
IPDisplay.Markdown(f"""
{__toc.title(1, 1)}
---
""")


# 2.2. Driver program
---


In [17]:
import line_profiler as lp

# Dummy run to trigger any JIT and avoid the overhead during profiling
main()

pr = lp.LineProfiler()
pr.add_function(matMulElem)
pr.add_function(matMul)
pr.add_function(runMainLowL)
pr.add_function(runMainHighL)
prMain = pr(main)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/matMul.lprof")

In [18]:
prof = lp.load_stats("kernProfOut/matMul.lprof")

with open("kernProfOut/matMul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [19]:
with open("kernProfOut/matMul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [20]:
IPDisplay.Markdown(__toc.display(2, 0))

# 3.1. Array programming
---
1. Toy problem
2. Profiling
3. __Vectorisation__
	1. __Array programming__
		1. Indexing
		2. Broadcasting
	2. SIMD
4. Parallel execution
5. Wrapping up


In [21]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0)}
---
New paradigm :
- The "atoms" you manipulate are arrays, not their individual elements anymore
- Apply operations on entire arrays at once
- (Don't freak out, everyone needs some time to adapt)

Effects:
- Reduces loops overhead
- Relies on highly optimised subroutines
    - Coded in C (hence compiled), conveniently packaged in python modules
- __Python code remains high-level__ (details are abstracted away)
""")


# 3.1. Array programming
---
New paradigm :
- The "atoms" you manipulate are arrays, not their individual elements anymore
- Apply operations on entire arrays at once
- (Don't freak out, everyone needs some time to adapt)

Effects:
- Reduces loops overhead
- Relies on highly optimised subroutines
    - Coded in C (hence compiled), conveniently packaged in python modules
- __Python code remains high-level__ (details are abstracted away)


In [22]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0)}
---
""")


# 3.1. Array programming
---


In [23]:
def betterMatMulElem(aRow, bCol):
    ab = aRow * bCol  # element-wise operation
    cij = np.sum(ab)  # reduction operation
    return cij

- No more loops
- No need to use `l` anymore
    - Both arrays are vectors of size `l`
    - __Warning:__ don't mess the shape of your arrays
- Uses (one of) numpy reduction operations
    - sum, prod, max, min, mean, std, ...
    - In _n_ dimensions you can choose the axis on which to perform the reduction

In [24]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0)}
---
""")


# 3.1. Array programming
---


In [25]:
def betterMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    C = np.empty((m, n), dtype=A.dtype)
    for i in range(m):
        for j in range(n):
            C[i, j] = betterMatMulElem(A[i, :], B[:, j])
    return C

In [26]:
def runBetterMainLowL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesLowL:
            C = betterMatMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def runBetterMainHighL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesHighL:
            C = betterMatMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def betterMain():
    runBetterMainLowL()
    runBetterMainHighL()


# Dummy run to trigger any JIT and avoid the overhead during profiling
betterMain()

pr = lp.LineProfiler()
pr.add_function(betterMatMulElem)
pr.add_function(betterMatMul)
pr.add_function(runBetterMainLowL)
pr.add_function(runBetterMainHighL)
prMain = pr(betterMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/betterMatMul.lprof")

prof = lp.load_stats("kernProfOut/betterMatMul.lprof")
with open("kernProfOut/betterMatMul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

In [27]:
with open("kernProfOut/betterMatMul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [28]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0)}
---
That seems simple enough.

Can we go one step further ? Can we __remove__ all loops ?

__YES__. Array programming is meant for that and provides you with different techniques to achieve this goal. We will see two of them:
- __Indexing__ an array with other arrays of indices
- __Broadcasting__ arrays of different shapes
""")


# 3.1. Array programming
---
That seems simple enough.

Can we go one step further ? Can we __remove__ all loops ?

__YES__. Array programming is meant for that and provides you with different techniques to achieve this goal. We will see two of them:
- __Indexing__ an array with other arrays of indices
- __Broadcasting__ arrays of different shapes


In [29]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0, 0)}
---
""")


# 3.1.1. Indexing
---


In [30]:
def noLoopMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    i = np.arange(m, dtype=np.int32)  # [0, 1, 2, ... m-1]
    i = np.repeat(i, n)  # [0, 0, 0, ... 1, 1, 1, ...]
    j = np.arange(n, dtype=np.int32)  # [0, 1, 2, ... n-1]
    j = np.tile(j, m)  # [0, 1, 2, ... 0, 1, 2, ...]
    C = np.empty((m, n), dtype=A.dtype)
    aRows = A[i, :]
    #assert aRows.shape == (m*n, l)  # the shaaaaapes !
    bCols = B[:, j]
    #assert bCols.shape == (l, m*n)  # check theeeem !!
    # i, j = (0, 0), (0, 1), (0, 2), ... (1, 0), (1, 1), (1, 2), ...
    C[i, j] = np.sum(aRows * bCols.T, axis=1)
    return C

In [31]:
def runNoLoopMainLowL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesLowL:
            C = noLoopMatMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def runNoLoopMainHighL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesHighL:
            C = noLoopMatMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def noLoopMain():
    runNoLoopMainLowL()
    runNoLoopMainHighL()


# Dummy run to trigger any JIT and avoid the overhead during profiling
noLoopMain()

pr = lp.LineProfiler()
pr.add_function(noLoopMatMul)
pr.add_function(runNoLoopMainLowL)
pr.add_function(runNoLoopMainHighL)
prMain = pr(noLoopMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/noLoopMatMul.lprof")

prof = lp.load_stats("kernProfOut/noLoopMatMul.lprof")
with open("kernProfOut/noLoopMatMul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

In [32]:
with open("kernProfOut/noLoopMatMul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [33]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0, 0)}
---
No loops through indexing seems to have some potential:
- Good performances when the matrices are small
- But __terrible__ when the matrices get bigger. Why is that ?

__Indexing__ arrays is ok unless it means __replicating__ data beyond reason

`aRows.shape == (m*n, l)` and `bCols.shape == (l, m*n)` means allocating a lot of additional memory to store redundant data. It also means that `np.sum` has to work on large arrays, slowing the process even further.

How to deal with this situation ?
""")


# 3.1.1. Indexing
---
No loops through indexing seems to have some potential:
- Good performances when the matrices are small
- But __terrible__ when the matrices get bigger. Why is that ?

__Indexing__ arrays is ok unless it means __replicating__ data beyond reason

`aRows.shape == (m*n, l)` and `bCols.shape == (l, m*n)` means allocating a lot of additional memory to store redundant data. It also means that `np.sum` has to work on large arrays, slowing the process even further.

How to deal with this situation ?


In [34]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0, 1)}
---
#### What about broadcasting ?
__Concept:__
- Binary (element-wise) operations such as the multiplication will fail on two arrays of different shapes. Unless these shapes can be __broadcasted__ together.
- Imagine matrices $A_{'{'}(m, l){'}'}$, $B_{'{'}(l, n){'}'}$ and a vector $V_{'{'}(l){'}'}$
- `A * V` is accepted, numpy will multiply each (whole) column $j$ of $A$ with $v_j$
- In other words, numpy wil __broadcast__ $v$ along the rows of $A$
- However `B * V` and `V * B` are not accepted, but `V.reshape(l, 1) * B` will multiply each row $i$ with $v_i$
- In other words, numpy wil __broadcast__ $v$ along the columns of $B$
""")


# 3.1.2. Broadcasting
---
#### What about broadcasting ?
__Concept:__
- Binary (element-wise) operations such as the multiplication will fail on two arrays of different shapes. Unless these shapes can be __broadcasted__ together.
- Imagine matrices $A_{(m, l)}$, $B_{(l, n)}$ and a vector $V_{(l)}$
- `A * V` is accepted, numpy will multiply each (whole) column $j$ of $A$ with $v_j$
- In other words, numpy wil __broadcast__ $v$ along the rows of $A$
- However `B * V` and `V * B` are not accepted, but `V.reshape(l, 1) * B` will multiply each row $i$ with $v_i$
- In other words, numpy wil __broadcast__ $v$ along the columns of $B$


In [35]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0, 1)}
---
#### What about broadcasting ?

Broadcasting arrays with the same (number of) dimensions/axis is possible if:
- All dimensions are equal (hence no need for broadcast)
- For any pair of respective dimensions that differ, one is equal to 1 (then the array is broadcasted along that axis)

Broadcast of arrays of different (number of) dimensions/axis is also possible, but can be misleading/counterintuitive

__Better safe than sorry:__ always reshape your arrays with 1's such that the number of axis is the same.
""")


# 3.1.2. Broadcasting
---
#### What about broadcasting ?

Broadcasting arrays with the same (number of) dimensions/axis is possible if:
- All dimensions are equal (hence no need for broadcast)
- For any pair of respective dimensions that differ, one is equal to 1 (then the array is broadcasted along that axis)

Broadcast of arrays of different (number of) dimensions/axis is also possible, but can be misleading/counterintuitive

__Better safe than sorry:__ always reshape your arrays with 1's such that the number of axis is the same.


In [36]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0, 1)}
---
#### What about broadcasting <u>in practice</u> ?
""")


# 3.1.2. Broadcasting
---
#### What about broadcasting <u>in practice</u> ?


In [37]:
def betterNoLoopMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    C = A.reshape(m, l, 1) * B.reshape(1, l, n)
    #assert C.shape == (m, l, n)  # you definitely want to check that shape
    C = np.sum(C, axis=1)  # apply the reduction along the second axis
    #assert C.shape == (m, n)  # The shape. Check again
    return C

In [38]:
def runBetterNoLoopMainLowL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesLowL:
            C = betterNoLoopMatMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def runBetterNoLoopMainHighL():
    for _ in range(nRuns):  # !! Make several runs
        for A, B, expected in matricesHighL:
            C = betterNoLoopMatMul(A, B)
            # test the result (working code > fast code)
            assert np.allclose(C, expected)
            
def betterNoLoopMain():
    runBetterNoLoopMainLowL()
    runBetterNoLoopMainHighL()


# Dummy run to trigger any JIT and avoid the overhead during profiling    
betterNoLoopMain()

pr = lp.LineProfiler()
pr.add_function(betterNoLoopMatMul)
pr.add_function(runBetterNoLoopMainLowL)
pr.add_function(runBetterNoLoopMainHighL)
prMain = pr(betterNoLoopMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/betterNoLoopMatMul.lprof")

prof = lp.load_stats("kernProfOut/betterNoLoopMatMul.lprof")
with open("kernProfOut/betterNoLoopMatMul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

In [39]:
with open("kernProfOut/betterNoLoopMatMul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [40]:
IPDisplay.Markdown(f"""
{__toc.title(2, 0)}
---
Can we __compile__ on top of array programming ?
""")


# 3.1. Array programming
---
Can we __compile__ on top of array programming ?


In [41]:
import numba as nb

@nb.jit(nopython=True)
def JITMatMulElem(aRow, bCol):
    ab = aRow * bCol
    cij = np.sum(ab)
    return cij

In [42]:
def JITMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    C = np.empty((m, n), dtype=A.dtype)
    for i in range(m):
        for j in range(n):
            C[i, j] = JITMatMulElem(A[i, :], B[:, j])
    return C

@nb.jit(nopython=True)
def ALLJITMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    C = np.empty((m, n), dtype=A.dtype)
    #assert l == ll  # check the shapes during dev.
    for i in range(m):
        for j in range(n):
            C[i, j] = JITMatMulElem(A[i, :], B[:, j])
    return C

In [43]:
def runJITMainLowL():
    for _ in range(nRuns):
        for A, B, expected in matricesLowL:
            JITC = JITMatMul(A, B)
            ALLJITC = ALLJITMatMul(A, B)
            assert np.allclose(JITC, expected)
            assert np.allclose(ALLJITC, expected)
            
def runJITMainHighL(): 
    for _ in range(nRuns):
        for A, B, expected in matricesHighL:
            JITC = JITMatMul(A, B)
            ALLJITC = ALLJITMatMul(A, B)
            assert np.allclose(JITC, expected)
            assert np.allclose(ALLJITC, expected)
            
def JITMain():
    runJITMainLowL()
    runJITMainHighL()


# Dummy run to trigger any JIT and avoid the overhead during profiling
JITMain()

pr = lp.LineProfiler()
pr.add_function(JITMatMul)
pr.add_function(runJITMainHighL)
pr.add_function(runJITMainLowL)
prMain = pr(JITMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/JITMatmul.lprof")

prof = lp.load_stats("kernProfOut/JITMatmul.lprof")
with open("kernProfOut/JITMatmul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [44]:
with open("kernProfOut/JITMatmul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [45]:
IPDisplay.Markdown(__toc.display(2, 1))

# 3.2. SIMD
---
1. Toy problem
2. Profiling
3. __Vectorisation__
	1. Array programming
	2. __SIMD__
		1. Data type
		2. Memory layout
4. Parallel execution
5. Wrapping up


In [46]:
IPDisplay.Markdown(f"""
{__toc.title(2, 1)}
---
- Same Instruction Multiple Data
- Human: Operations are applied on the __elements__ of an array
- Machine: Operations are applied on a __register__ of 8/16/32/64 bits (and beyond)
- SIMD: Fit as many elements as possible in a register and apply the operation __*once*__
- Not possible without _unrolling_ a loop
    - Possible to do it at low level (C/C++, assembly, ...)
    - In python, handled by libraries such as numpy, tensorflow, pytorch, ...

The gain in speed depends on the size of your data and the size of the registers.
It is useful on a CPU, but on a GPU the registers are __A LOT__ larger
""")


# 3.2. SIMD
---
- Same Instruction Multiple Data
- Human: Operations are applied on the __elements__ of an array
- Machine: Operations are applied on a __register__ of 8/16/32/64 bits (and beyond)
- SIMD: Fit as many elements as possible in a register and apply the operation __*once*__
- Not possible without _unrolling_ a loop
    - Possible to do it at low level (C/C++, assembly, ...)
    - In python, handled by libraries such as numpy, tensorflow, pytorch, ...

The gain in speed depends on the size of your data and the size of the registers.
It is useful on a CPU, but on a GPU the registers are __A LOT__ larger


In [47]:
IPDisplay.Markdown(f"""
{__toc.title(2, 1, 0)}
---
""")


# 3.2.1. Data type
---


In [48]:
def runSIMDMainLowL():
    for _ in range(nRuns):
        for A, B, expected in matricesLowL:
            A64, B64 = A.astype(np.float64), B.astype(np.float64)
            C1 = ALLJITMatMul(A64, B64)
            C2 = betterNoLoopMatMul(A64, B64)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            
            A32, B32 = A.astype(np.float32), B.astype(np.float32)
            C1 = ALLJITMatMul(A32, B32)
            C2 = betterNoLoopMatMul(A32, B32)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            

In [49]:
IPDisplay.Markdown(f"""
{__toc.title(2, 1, 0)}
---
""")


# 3.2.1. Data type
---


In [50]:
def runSIMDMainHighL(): 
    for _ in range(nRuns):
        for A, B, expected in matricesHighL:
            A64, B64 = A.astype(np.float64), B.astype(np.float64)
            C1 = ALLJITMatMul(A64, B64)
            C2 = betterNoLoopMatMul(A64, B64)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            
            A32, B32 = A.astype(np.float32), B.astype(np.float32)
            C1 = ALLJITMatMul(A32, B32)
            C2 = betterNoLoopMatMul(A32, B32)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)

In [51]:
def SIMDMain():
    runSIMDMainLowL()
    runSIMDMainHighL()


# Dummy run to trigger any JIT and avoid the overhead during profiling
SIMDMain()


pr = lp.LineProfiler()
pr.add_function(runSIMDMainLowL)
pr.add_function(runSIMDMainHighL)
prMain = pr(SIMDMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/SIMDMatmul.lprof")

prof = lp.load_stats("kernProfOut/SIMDMatmul.lprof")
with open("kernProfOut/SIMDMatmul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [52]:
with open("kernProfOut/SIMDMatmul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [53]:
IPDisplay.Markdown(f"""
{__toc.title(2, 1, 1)}
---
- Same Instruction Multiple Data
- First step is to fetch data from memory
- Faster if the data is contiguous in memory
    - In memory, everything is in one dimension
    - Matrix is in two, two adjacent elements may not be contiguous
- __Row-major :__ (_aka_ C-style arrays)
    - Elements on a same __line__ are contiguous
    - __Lines__ are written consecutively in memory (as if concatenated)
- __Column-major :__ (_aka_ Fortran-style arrays)
    - Elements on a same __column__ are contiguous
    - __Columns__ are written consecutively in memory (as if concatenated)

__Contiguous case :__ copying a block of memory directly in the register (1 instruction)

__Non-contiguous (sparse) case :__ fetch individual elements from memory to fill the register ($n\geq 1$ instructions)
""")


# 3.2.2. Memory layout
---
- Same Instruction Multiple Data
- First step is to fetch data from memory
- Faster if the data is contiguous in memory
    - In memory, everything is in one dimension
    - Matrix is in two, two adjacent elements may not be contiguous
- __Row-major :__ (_aka_ C-style arrays)
    - Elements on a same __line__ are contiguous
    - __Lines__ are written consecutively in memory (as if concatenated)
- __Column-major :__ (_aka_ Fortran-style arrays)
    - Elements on a same __column__ are contiguous
    - __Columns__ are written consecutively in memory (as if concatenated)

__Contiguous case :__ copying a block of memory directly in the register (1 instruction)

__Non-contiguous (sparse) case :__ fetch individual elements from memory to fill the register ($n\geq 1$ instructions)


In [54]:
def runOrderedSIMDMainLowL():
    for _ in range(nRuns):
        for A, B, expected in matricesLowL:
            A32F, B32C = np.asarray(A, dtype=np.float32, order='F'), np.asarray(B, dtype=np.float32, order='C')
            C1 = ALLJITMatMul(A32F, B32C)
            C2 = betterNoLoopMatMul(A32F, B32C)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            
            A32C, B32F = np.asarray(A, dtype=np.float32, order='C'), np.asarray(B, dtype=np.float32, order='F')
            C1 = ALLJITMatMul(A32C, B32F)
            C2 = betterNoLoopMatMul(A32C, B32F)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            
def runOrderedSIMDMainHighL():
    for _ in range(nRuns):
        for A, B, expected in matricesHighL:
            A32F, B32C = np.asarray(A, dtype=np.float32, order='F'), np.asarray(B, dtype=np.float32, order='C')
            C1 = ALLJITMatMul(A32F, B32C)
            C2 = betterNoLoopMatMul(A32F, B32C)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            
            A32C, B32F = np.asarray(A, dtype=np.float32, order='C'), np.asarray(B, dtype=np.float32, order='F')
            C1 = ALLJITMatMul(A32C, B32F)
            C2 = betterNoLoopMatMul(A32C, B32F)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)

In [55]:
def orderedSIMDbetterMain():
    runOrderedSIMDMainLowL()
    runOrderedSIMDMainHighL()


# Dummy run to trigger any JIT and avoid the overhead during profiling
orderedSIMDbetterMain()

pr = lp.LineProfiler()
pr.add_function(runOrderedSIMDMainLowL)
pr.add_function(runOrderedSIMDMainHighL)
prMain = pr(orderedSIMDbetterMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/orderedSIMDMatmul.lprof")

In [56]:
prof = lp.load_stats("kernProfOut/orderedSIMDMatmul.lprof")

with open("kernProfOut/orderedSIMDMatmul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [57]:
with open("kernProfOut/orderedSIMDMatmul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [58]:
IPDisplay.Markdown(f"""
{__toc.title(2)}
---
##### What did we learn ?
- Array programming is great, but use it with caution
    - The best approach may not be easy/intuitive (thinking in $n$ dimensions)
    - Compiled loops may be faster than no loop at all
    - Especially if using indexing/masking techniques
""")


# 3. Vectorisation
---
##### What did we learn ?
- Array programming is great, but use it with caution
    - The best approach may not be easy/intuitive (thinking in $n$ dimensions)
    - Compiled loops may be faster than no loop at all
    - Especially if using indexing/masking techniques


In [59]:
IPDisplay.Markdown(f"""
{__toc.title(2)}
---
##### What did we learn ?
- The data type is important
    - Do not use large datatypes if you don't need it
    - Be aware that on some GPUs, float64 is not available (only float32)
    - Operations on ints are faster, if you don't need floats, don't use them
- The order of multi-dimensional arrays may drastically impact performance
    - If you know in advance how you will address your arrays, use that knowledge
    - In doubt, compare the trade-offs of converting arrays _Vs._ apply operation in a sub-optimal way
    
__WARNING :__ Such optimisation is specific to using arrays and is often very local. It is easy to loose track of time and waste precious development work optimising small details of your code.

__Always__ profile at higher level (_e.g._ using `cProfile`) to focus your efforts on real bottlenecks _first_.
""")


# 3. Vectorisation
---
##### What did we learn ?
- The data type is important
    - Do not use large datatypes if you don't need it
    - Be aware that on some GPUs, float64 is not available (only float32)
    - Operations on ints are faster, if you don't need floats, don't use them
- The order of multi-dimensional arrays may drastically impact performance
    - If you know in advance how you will address your arrays, use that knowledge
    - In doubt, compare the trade-offs of converting arrays _Vs._ apply operation in a sub-optimal way
    
__WARNING :__ Such optimisation is specific to using arrays and is often very local. It is easy to loose track of time and waste precious development work optimising small details of your code.

__Always__ profile at higher level (_e.g._ using `cProfile`) to focus your efforts on real bottlenecks _first_.


In [60]:
IPDisplay.Markdown(__toc.display(3, 0))

# 4.1. Multi-threading/processing
---
1. Toy problem
2. Profiling
3. Vectorisation
4. __Parallel execution__
	1. __Multi-threading/processing__
		1. Concepts
		2. The python situation
	2. Data & Memory
5. Wrapping up


In [61]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0, 0)}
---
__Multi-processing :__
- Your program (a process) can __fork__ (_i.e._ duplicate itself) to create child processes
- Each process handles privately its own memory and resources. __The OS ensures that privacy__
- __Inter-process communication__ is done through __pipes__, files, message queues __(_e.g._ MPI)__, sockets (_e.g._ the network), __shared memory__
     
__Multi-threading :__
- Your program (a process) can __spawn__ several threads of execution
- They are not different processes, they can access the same memory and resources
- Lighter and more powerful than multi-processing, but comes with added complexity
    - _Concurrent access_ to resources
    - Issues related to _race conditions_, (_e.g._ deadlocks, starvation, ...)
    - Needs a good understanding of __locks__ (mutex), semaphores, __barriers__ ...
""")


# 4.1.1. Concepts
---
__Multi-processing :__
- Your program (a process) can __fork__ (_i.e._ duplicate itself) to create child processes
- Each process handles privately its own memory and resources. __The OS ensures that privacy__
- __Inter-process communication__ is done through __pipes__, files, message queues __(_e.g._ MPI)__, sockets (_e.g._ the network), __shared memory__
     
__Multi-threading :__
- Your program (a process) can __spawn__ several threads of execution
- They are not different processes, they can access the same memory and resources
- Lighter and more powerful than multi-processing, but comes with added complexity
    - _Concurrent access_ to resources
    - Issues related to _race conditions_, (_e.g._ deadlocks, starvation, ...)
    - Needs a good understanding of __locks__ (mutex), semaphores, __barriers__ ...


In [62]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0, 1)}
---
Multi-threading exists in python, __BUT__ :
- Python does not want race conditions, deadlocks nor any related issues
- The only way to ensure this (at python level) is by synchronising all operations
- This is possible through the use of the __GIL (Global Interpreter Lock)__
    - All (python) instructions have to 
        1. Lock the GIL (automatic)
        2. Execute (this is your code)
        3. Release the GIL (automatic)
    - Concurrent threads are put on hold until they lock the GIL
- Consequently, only one thread at a time can run

Multi-processing also exists in python :
- A python _process_ is not only your code, but also the full interpreter executing it
- Several processes imply several instances of the interpreter, hence several GIL
- Only way to achieve "true" parallelisation in python

""")


# 4.1.2. The python situation
---
Multi-threading exists in python, __BUT__ :
- Python does not want race conditions, deadlocks nor any related issues
- The only way to ensure this (at python level) is by synchronising all operations
- This is possible through the use of the __GIL (Global Interpreter Lock)__
    - All (python) instructions have to 
        1. Lock the GIL (automatic)
        2. Execute (this is your code)
        3. Release the GIL (automatic)
    - Concurrent threads are put on hold until they lock the GIL
- Consequently, only one thread at a time can run

Multi-processing also exists in python :
- A python _process_ is not only your code, but also the full interpreter executing it
- Several processes imply several instances of the interpreter, hence several GIL
- Only way to achieve "true" parallelisation in python



In [63]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0)}
---
""")


# 4.1. Multi-threading/processing
---


In [64]:
import multiprocessing as mp
import psutil

# on a cluster the number of CPU-cores <= number of usable cores
threadNum = len(psutil.Process().cpu_affinity())
#threadNum = os.cpu_count()

In [65]:
# Don't mind this code
# (this cell is hidden from the preentation)

#  On my computer I want to ensure I don't use hyper-threaded cpu cores, 
#  so I fix the number of usable threads to a lower number
#  (I have 4 efficient cores (=> 8 virtual ones), and 8 performant ones
#      amounting to 16, I divide by 2 to get the number of preformant cores I wish to use)
# This is to be sure that profiling results are consistents (all processes run on the same type of core)
threadNum = threadNum//2

In [66]:
@nb.jit(nopython=True)
def parallelJITMatMulElem(args):
    aRow, bCol = args
    ab = aRow * bCol
    cij = np.sum(ab)
    return cij

In [67]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0)}
---
""")


# 4.1. Multi-threading/processing
---


In [68]:
def parallelMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    C = np.empty((m, n), dtype=A.dtype)
    chunksize = int(np.ceil(m*n/threadNum))
    # Avoid spawning processes directly, use a pool
    with mp.Pool(threadNum) as pool:
        it = ((A[i, :], B[:, j]) for i in range(m) for j in range(n))
        C.flat = list(pool.imap(parallelJITMatMulElem, it, chunksize=chunksize))
    pool.join()  # Wait for all processes to complete
    return C

In [69]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0)}
---
""")


# 4.1. Multi-threading/processing
---


In [70]:
@nb.jit(nopython=True)
def parallelJITMatMulRow(args):
    aRow, B = args
    ab = aRow[:, np.newaxis] * B
    ci = np.sum(ab, axis=0)
    return ci

def rowParallelMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    C = np.empty((m, n), dtype=A.dtype)
    # on a cluster the number of CPU-cores <= number of usable cores
    chunksize = int(np.ceil(m/threadNum))
    with mp.Pool(threadNum) as pool:
        it = ((A[i, :], B) for i in range(m))
        C[:, :] = list(pool.imap(parallelJITMatMulRow, it, chunksize=chunksize))
    pool.join()
    return C

In [71]:
IPDisplay.Markdown(f"""
{__toc.title(3, 0)}
---
""")


# 4.1. Multi-threading/processing
---


In [72]:
nb.config.NUMBA_NUM_THREADS = threadNum

@nb.jit(nopython=True, parallel=True)
def parallelALLJITMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    C = np.empty((m, n), dtype=A.dtype)
    #assert l == ll  # check the shapes during dev.
    for i in nb.prange(m):
        C[i, :] = parallelJITMatMulRow((A[i, :], B))
    return C

In [73]:
def runParallelMainLowL():
    for _ in range(nRuns):
        for A, B, expected in matricesLowL:
            A32C, B32F = np.asarray(A, dtype=np.float32, order='C'), np.asarray(B, dtype=np.float32, order='F')
            C1 = parallelMatMul(A32C, B32F)
            C2 = rowParallelMatMul(A32C, B32F)
            C3 = parallelALLJITMatMul(A32C, B32F)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            assert np.allclose(C3, expected)
            
def runParallelMainHighL():
    for _ in range(nRuns):
        for A, B, expected in matricesHighL:
            A32C, B32F = np.asarray(A, dtype=np.float32, order='C'), np.asarray(B, dtype=np.float32, order='F')
            C1 = parallelMatMul(A32C, B32F)
            C2 = rowParallelMatMul(A32C, B32F)
            C3 = parallelALLJITMatMul(A32C, B32F)
            assert np.allclose(C1, expected)
            assert np.allclose(C2, expected)
            assert np.allclose(C3, expected)

def parallelMain():
    runParallelMainLowL()
    runParallelMainHighL()
    

In [74]:
# Dummy run to trigger any JIT and avoid the overhead during profiling
parallelMain()

pr = lp.LineProfiler()
pr.add_function(parallelMatMul)
pr.add_function(rowParallelMatMul)
pr.add_function(runParallelMainLowL)
pr.add_function(runParallelMainHighL)
prMain = pr(parallelMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/parallelMatmul.lprof")

In [75]:
prof = lp.load_stats("kernProfOut/parallelMatmul.lprof")

with open("kernProfOut/parallelMatmul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [76]:
with open("kernProfOut/parallelMatmul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [77]:
IPDisplay.Markdown(__toc.display(3, 1))

# 4.2. Data & Memory
---
1. Toy problem
2. Profiling
3. Vectorisation
4. __Parallel execution__
	1. Multi-threading/processing
	2. __Data & Memory__
		1. Shared memory Vs messages
		2. Concurrent access
5. Wrapping up


In [78]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 0)}
---
Remember, processes have to communicate.

That communication is implicitly handled for you by the multiprocessing libray:
1. The function to run and its arguments are serialised
2. The child processes are created and receive a message consisting in the serialised code and data
3. Each child process de-serialises the received function to execute and applies it on the data
4. The returned value (even if None) is serialised and sent back to the parent process

""")


# 4.2.1. Shared memory Vs messages
---
Remember, processes have to communicate.

That communication is implicitly handled for you by the multiprocessing libray:
1. The function to run and its arguments are serialised
2. The child processes are created and receive a message consisting in the serialised code and data
3. Each child process de-serialises the received function to execute and applies it on the data
4. The returned value (even if None) is serialised and sent back to the parent process



In [79]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 0)}
---
Remember, processes have to communicate.

If the data is too large, that approach can become slow and/or consume too much memory, since (part of) the original data is copied by each process.

You can choose to avoid this by storing your data in a part of the memory you allow to be shared with the child processes.
- Access to the data will be slower (since it is no longer local in each process)
- __But__ the time for a child process to start will be shorter __and the same regardless of the size of your data__
- Profile and choose the best approach for your use-case, it really depends on your data and what you do with it
""")


# 4.2.1. Shared memory Vs messages
---
Remember, processes have to communicate.

If the data is too large, that approach can become slow and/or consume too much memory, since (part of) the original data is copied by each process.

You can choose to avoid this by storing your data in a part of the memory you allow to be shared with the child processes.
- Access to the data will be slower (since it is no longer local in each process)
- __But__ the time for a child process to start will be shorter __and the same regardless of the size of your data__
- Profile and choose the best approach for your use-case, it really depends on your data and what you do with it


In [80]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 1)}
---
Sharing memory is a great way to reduce memory consumption and speed up parallel code. But you need to be cautious.

_What happens if two processes try to access the same data at the same time ?_
Well, that is exactly the kind of issue the GIL solves.
1. __Write__ and __Write__ : you either corrupted your data or erased a returned value with another
2. __Write__ and __Read__ : the writing process should be fine, but the data read by the reading process is most likely corrupted
3. __Read__ and __Read__ : this is ok, the data is not modified, so both processes read consistent data

By default, shared memory allocated through the multiprocessing library is protected by __locks__.
- In case of doubt, you can safely ignore these problems and simply allocate some shared memory.
- But then only one process at a time can access the shared memory.
- It could still be faster since you skip the serialisation + message passing step
""")


# 4.2.2. Concurrent access
---
Sharing memory is a great way to reduce memory consumption and speed up parallel code. But you need to be cautious.

_What happens if two processes try to access the same data at the same time ?_
Well, that is exactly the kind of issue the GIL solves.
1. __Write__ and __Write__ : you either corrupted your data or erased a returned value with another
2. __Write__ and __Read__ : the writing process should be fine, but the data read by the reading process is most likely corrupted
3. __Read__ and __Read__ : this is ok, the data is not modified, so both processes read consistent data

By default, shared memory allocated through the multiprocessing library is protected by __locks__.
- In case of doubt, you can safely ignore these problems and simply allocate some shared memory.
- But then only one process at a time can access the shared memory.
- It could still be faster since you skip the serialisation + message passing step


In [81]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1, 1)}
---
Sharing memory is a great way to reduce memory consumption and speed up parallel code. But you need to be cautious.

If you know what you are doing, you can disable this lock.
- Matrices A and B are never __written to__, only __read from__ (sc. 3.)
- Matrix C is only __written to__ (by the child processes) (sc. 1. ?)
- Different child processes never write on the same cell of the matrix C (not sc. 1. ?)

Is it safe to disable the lock on C ? 
""")


# 4.2.2. Concurrent access
---
Sharing memory is a great way to reduce memory consumption and speed up parallel code. But you need to be cautious.

If you know what you are doing, you can disable this lock.
- Matrices A and B are never __written to__, only __read from__ (sc. 3.)
- Matrix C is only __written to__ (by the child processes) (sc. 1. ?)
- Different child processes never write on the same cell of the matrix C (not sc. 1. ?)

Is it safe to disable the lock on C ? 


In [82]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1)}
---
Time to use the big guns
""")


# 4.2. Data & Memory
---
Time to use the big guns


In [83]:
def produceMatrices(m, n, l):
    A = np.asarray(np.random.rand(m, l), dtype=np.float32, order='C')
    B = np.asarray(np.random.rand(l, n), dtype=np.float32, order='F')
    return A, B

matrices = [  # !! Use the same data across different runs
    produceMatrices(200, 400, 100000)
    for _ in range(3)  # !! Have several (different) samples
]

In [84]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1)}
---
""")


# 4.2. Data & Memory
---


In [85]:
def initPool(AArray, BArray, CArray):
    global A  # declare A, B and C global across the processes
    global B
    global C
    A = AArray  # These arrays need to be stored in shared memory
    B = BArray
    C = CArray

def parallelMatMulElemInPlace(args):
    i, j = args
    ab = A[i, :] * B[:, j]
    C[i, j] = np.sum(ab)

In [86]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1)}
---
""")


# 4.2. Data & Memory
---


In [87]:
f32Type = np.ctypeslib.as_ctypes_type(np.float32)


def parallelSharedMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    CBase = mp.Array(f32Type, m*n, lock=False)
    C = np.frombuffer(CBase, A.dtype).reshape(m, n)
    chunksize = int(np.ceil(m*n/threadNum))
    with mp.Pool(threadNum, initializer=initPool, initargs=(A, B, C)) as pool:
        it = ((i, j) for i in range(m) for j in range(n))
        list(pool.imap(parallelMatMulElemInPlace, it, chunksize=chunksize))
    pool.join()
    return C

In [88]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1)}
---
""")


# 4.2. Data & Memory
---


In [89]:
def parallelMatMulRowInPlace(args):
    i, = args
    ab = A[i, :][:, np.newaxis] * B
    C[i, :] = np.sum(ab, axis=0)

def rowParallelSharedMatMul(A, B):
    (m, l) = A.shape
    (ll, n) = B.shape
    #assert l == ll  # check the shapes during dev.
    CBase = mp.Array(f32Type, m*n, lock=False)
    C = np.frombuffer(CBase, A.dtype).reshape(m, n)
    chunksize = int(np.ceil(m/threadNum))
    with mp.Pool(threadNum, initializer=initPool, initargs=(A, B, C)) as pool:
        it = ((i,) for i in range(m))
        list(pool.imap(parallelMatMulRowInPlace, it, chunksize=chunksize))
    pool.join()
    return C

In [90]:
IPDisplay.Markdown(f"""
{__toc.title(3, 1)}
---
""")


# 4.2. Data & Memory
---


In [91]:
def parallelSharedMain():
    for _ in range(3):
        for A, B in matrices:
            A32Base, B32Base = mp.Array(f32Type, A.flat, lock=False), mp.Array(f32Type, B.flat, lock=False)
            AFlat, BFlat = np.frombuffer(A32Base, dtype=np.float32), np.frombuffer(B32Base, dtype=np.float32)
            AShared, BShared = AFlat.reshape(A.shape), BFlat.reshape(B.shape)
            C1 = rowParallelMatMul(A, B)
            C2 = parallelSharedMatMul(AShared, BShared)
            C3 = rowParallelSharedMatMul(AShared, BShared)
            C4 = parallelALLJITMatMul(A, B)
            expected = A@B
            assert np.allclose(C1, expected, atol=1.)
            assert np.allclose(C2, expected, atol=1.)
            assert np.allclose(C3, expected, atol=1.)
            assert np.allclose(C4, expected, atol=1.)
            

In [92]:
# Dummy run to trigger any JIT and avoid the overhead during profiling
parallelSharedMain()

pr = lp.LineProfiler()
prMain = pr(parallelSharedMain)
prMain()

# Generates a file containing statistics to be examined later :
pr.dump_stats("kernProfOut/parallelSharedMatmul.lprof")

In [93]:
prof = lp.load_stats("kernProfOut/parallelSharedMatmul.lprof")

with open("kernProfOut/parallelSharedMatmul.txt", "wt") as f:
    lp.show_text(prof.timings, prof.unit, stream=f)

#lp.show_text(prof.timings, prof.unit)

In [94]:
with open("kernProfOut/parallelSharedMatmul.txt", "rt") as f:
    text = f.read()

IPDisplay.HTML(f"""
<div class="full-width">
    <textarea rows="40" cols="120">
        {text}
    </textarea>
</div>
""")

In [95]:
IPDisplay.Markdown(__toc.display(4))

# 5. Wrapping up
---
1. Toy problem
2. Profiling
3. Vectorisation
4. Parallel execution
5. __Wrapping up__


In [98]:
IPDisplay.Markdown(f"""
{__toc.title(4)}
---
There are two ways to _"do more work per unit of time"_:
- Vectorise your data
    1. Good to speed up operations at low level
    2. Combine it with array programming
    3. Makes better use of computing resources
- Execute operations in parallel
    1. Augment the number of parallel workers
    2. Possibly heavy overhead
    3. If your data is large, use shared memory
    4. Better used at higher level
    4. More powerful if the worker code is heavy
""")


# 5. Wrapping up
---
There are two ways to _"do more work per unit of time"_:
- Vectorise your data
    1. Good to speed up operations at low level
    2. Combine it with array programming
    3. Makes better use of computing resources
- Execute operations in parallel
    1. Augment the number of parallel workers
    2. Possibly heavy overhead
    3. If your data is large, use shared memory
    4. Better used at higher level
    4. More powerful if the worker code is heavy


In [99]:
IPDisplay.Markdown(f"""
{__toc.title(4)}
---
What is the best strategy ? __None__. Each are good at something different.
As usual, test the different approaches and tradeoffs, profile and choose the best according to your specific use-case.

__Do not hesitate__ to use a <u>_sub-optimal_</u> solution but very <u>_easy/fast to develop_</u>. You can come back later to optimise further.

It _is_ counter-intuitive, but optimising a large project in successive passes yields better results than focusing efforts on localised bottlenecks (even truer if the development time allocated to optimisation is fixed).
""")


# 5. Wrapping up
---
What is the best strategy ? __None__. Each are good at something different.
As usual, test the different approaches and tradeoffs, profile and choose the best according to your specific use-case.

__Do not hesitate__ to use a <u>_sub-optimal_</u> solution but very <u>_easy/fast to develop_</u>. You can come back later to optimise further.

It _is_ counter-intuitive, but optimising a large project in successive passes yields better results than focusing efforts on localised bottlenecks (even truer if the development time allocated to optimisation is fixed).


In [97]:
#jupyter nbconvert --to slides multiProcDemo.ipynb --TagRemovePreprocessor.remove_input_tags="{'hide-input'}" --TagRemovePreprocessor.remove_single_output_tags='hide-output' --no-prompt --SlidesExporter.reveal_number='c/t' --post serve